In [84]:
from collections import Counter, defaultdict
from transformers import BertTokenizer,AutoModel, AutoTokenizer
import sentencepiece as spm
import pandas as pd
import heapq
import re
from typing import Iterable
import numpy as np
import pickle

from tokenizers import Tokenizer, models, pre_tokenizers, trainers

import nltk
from nltk.tokenize import WhitespaceTokenizer

# **Question1 Unicode_correction**

In [85]:
data = pd.read_csv('gu_100.txt', on_bad_lines='skip', header=None, encoding="utf-8", engine='python')
print(data.head())

                                                   0
0  ૯મી ઓગસ્ટ ૨૦૧૬ના રોજ આદિવાસી વિકાસ સંગઠન દ્વાર...
1  ગુરુવારે સવારે બેંકો ખુલતા પહેલા પ્રતિબંધિત નો...
2  ઈન્ડિયન આઈડલ 11ના આગામી એપિસોડમાં ઉદિત નારાયણ ...
3  દેશની ઉચ્ચ ન્યાયાલયે એસસી/એસટી એક્ટને અર્થહીન ...
4  આથી ઋષિકેશ નગરમાં વિરભદ્ર બંધના દ્વાર પાસે તે ...


In [86]:
# ALL these List are prepared with the help of internet.
matras = set(['ા', 'િ', 'ી', 'ુ', 'ૂ', 'ે', 'ૈ', 'ો', 'ૌ', 'ં', 'ઃ', 'ૃ', 'ૅ', 'ૉ'])
vyanjans = set(['ક', 'ખ', 'ગ', 'ઘ', 'ઙ', 'ચ', 'છ', 'જ', 'ઝ', 'ઞ', 'ય', 'શ', 'ટ', 'ઠ', 'ડ', 'ઢ', 'ણ', 'ર', 'ષ', 'ત', 'થ', 'દ', 'ધ', 'ન', 'લ', 'સ', 'પ', 'ફ', 'બ', 'ભ', 'મ', 'વ', 'હ', 'ળ', 'ક્ષ', 'જ્ઞ']
)
dic = {
    'ા': 'આ', 'િ': 'ઇ', 'ી': 'ઈ', 'ુ': 'ઉ',
    'ૂ': 'ઊ', 'ે': 'એ', 'ૈ': 'ઐ', 'ો': 'ઓ', 'ૌ': 'ઔ',
    'ં': 'અં', 'ઃ': 'અ:', 'ૃ': 'ઋ', 'ૅ': 'ઍ', 'ૉ': 'ઑ'
}
# Making dictionary to map matras with their swar sound.
swars = set(['અ', 'આ', 'ઇ', 'ઈ', 'ઉ', 'ઊ', 'એ', 'ઐ', 'ઓ', 'ઔ', 'અં', 'અ:', 'ઋ', 'ઍ', 'ઑ'])
punctuations = set(['>्','0्', '1्', '"्', 'ळ्', '2्', '–्', 'ः्', '3्', '5्', '4्',
                    '््', '%्', '—्', '8्', '6्', '7्', '9्', 'ॅ्', 'a्', 'e्', '#्',
                    'i्', 'r्', 't्', '»्', 'o्', 'n्', 'd्', '०्', 's्', 'h्',
                    'l्', 'c्', 'm्', '\u200c्', '\u200b्', 'ï्', 'A्', 'p्',
                    '•्', 'b्', 'G्', 'B्', '&्', 'u्', '_्', '@्', 'M्', 'о्',
                    'f्', '·्', '$्', 'S्', 'g्', 'I्', 'а्', 'е्', 'P्', 'и्',
                    'R्', 'y्', 'k्', 'w्', 'T्', '�्', 'a', 'b', 'c', 'd', 'e',
                    'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r',
                    's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '0', '1', '2', '3', '4',
                    '5', '6', '7', '8', '9', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H',
                    'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U',
                    'V', 'W', 'X', 'Y', 'Z', '!', '"', '\\', '#', '\\', '$', '%', '\\',
                    '&', "'", '\\', '(', '\\', ')', '\\', '*', '\\', '+', ',', '\\', '-',
                    '\\', '.', '/', ':', ';', '<', '=', '>', '\\', '?', '@', '\\', '[', '\\',
                    '\\', '\\', ']', '\\', '^', '_', '`', '\\', '{', '\\', '|', '\\', '}', '\\',
                    '~', '‘', '’', '“', '”', '૰', '।', '॥'])# These are noise we just have to insure these does'nt occur and even if these occurs we just ignore them.

# We created set of the list to imporve the look_up time as in sets lookup time if of O(1).


In [87]:
def remove_trivial_prefix_suffix(input_string):
    # Define regular expression pattern to match any sequence of characters from the specified set
    pattern = r'^(?:CLS|SEP|[\W_]+)|[\W_]+$'

    # Use re.sub() to remove the matched sequences from the beginning and end of the string
    result = re.sub(pattern, '', input_string)

    # Remove extra spaces, ".", "!", "?", or any other symbol
    result = re.sub(r'\s+', ' ', result)  # Remove extra spaces
    result = re.sub(r'[^\w\s]', '', result)  # Remove symbols except word characters and spaces

    return result


In [88]:
def unicode(word):
    Corrected_word = ""
    l = len(word)
    for i in range(l):
        if word[i] in vyanjans:
            Corrected_word += ' ' +  word[i]+'्'
            if i <= l-2 and (word[i+1]=='्' or word[i+1] in punctuations) :   # IF this condition satisfied then we are doing nothing.
                pass
            elif i <= l-2 and (word[i+1] in vyanjans or word[i+1] in swars):
                Corrected_word += ' '+'અ'
            elif i <= l-2 and word[i+1] in matras:
                Corrected_word += ' '+ dic[word[i+1]]
            elif i == l - 1:
                Corrected_word += ' ' + 'અ'
        elif word[i] in swars:
            Corrected_word += ' '+ word[i]
    return Corrected_word

In [89]:
for i in "ઓગસ્ટઓગ":   # code helpful for explanation of unicode function
    print(i)

print(unicode('ઓગસ્ટઓગ'))

ઓ
ગ
સ
્
ટ
ઓ
ગ
 ઓ ગ् અ સ् ટ् અ ઓ ગ् અ


# **Question 2**

Get Tokens With Frequency

In [90]:
# white_seperated_words count
# Create tokens
tokens = []
for i in data.iloc:
    for _ in i[0].split():
        if _ not in punctuations:
            if _[-1] in punctuations:           # to check for noise
                _ = _[:-1]
            tokens.append(_)
    tokens.append('$') # to signify end of sentence.

In [91]:
token_dict = Counter(tokens)
freq_words_token = heapq.nlargest(len(token_dict.keys()), token_dict, key=token_dict.get) # to print tokens in decreasing order of their occurances
print("Top 20 Token with frequency")
for i in freq_words_token[:20]:
    if i == '$':
        continue
    print(f"({i}, {token_dict[i]})")
# freq_words_token will contain all words in decreasing order of their frequency

#Uncomment below given code for all tokens    
# for i in freq_words_token:
#     if i == '$':
#         continue
#     print(f"({i}, {token_dict[i]})")

Top 20 Token with frequency
(છે, 139175)
(અને, 61469)
(આ, 41095)
(માટે, 33675)
(કે, 30223)
(પણ, 27435)
(એક, 24106)
(પર, 22321)
(તે, 20471)
(કરી, 20398)
(સાથે, 19291)
(જ, 18506)
(હતી, 18028)
(હતો, 12531)
(તો, 12141)
(નથી, 11597)
(હતા, 10900)
(કરવામાં, 10140)
(આવી, 9996)


Get Characters from tokens With Frequency

In [92]:
# Character_count
from collections import Counter
# char_list = [j for i in tokens for j in unicode(i).split()]
char_list = []
for i in tokens:
    if i == '$':
        continue
    for j in unicode(i).split():   #unicode_correction of tokens and counting characters
        char_list.append(j)
char_dict = Counter(char_list)

In [93]:
len(char_list)

16851472

In [94]:
freq_words_char = heapq.nlargest(len(char_dict.keys()), char_dict, key=char_dict.get)
print("Top 20 Characters with frequency")
for i in freq_words_char[:20]:
    print(f"({i}, {char_dict[i]})")

Top 20 Characters with frequency
(અ, 3194313)
(આ, 1766588)
(એ, 1134960)
(ર्, 997308)
(ન्, 823293)
(ઈ, 774391)
(ક्, 624158)
(મ्, 616744)
(ઓ, 575537)
(ત्, 545527)
(વ्, 540078)
(સ्, 448459)
(પ्, 405290)
(ઇ, 386727)
(ય्, 349844)
(લ्, 332040)
(ઉ, 312823)
(જ्, 268296)
(હ्, 254626)
(ટ्, 241932)


Get Syllables from tokens With Frequency

In [95]:
#syllable_count
def PurnaVyanjan(token,i):
    if  i < len(token) - 1:
        if token[i+1] in vyanjans:
            return token[i]
        elif token[i+1] in swars or token[i+1] in matras:
            return token[i:i+2]
        elif token[i+1] == '्':
            return token[i:i+2] + PurnaVyanjan(token,i+2)
    elif i >= len(token):
        return ""
    return token[i]

In [163]:
i=0
token = "જહાન્વી"
syllables_list = []
while i < len(token):
    if token[i] in vyanjans:
        string = PurnaVyanjan(token,i)
        syllables_list.append(string)
        i = i + len(string)-1
    elif token[i] in swars:
        syllables_list.append(token[i])
    i += 1

print(syllables_list)

['જ', 'હા', 'ન', 'વી']


In [96]:
# please also execute above purnavyanjan function.
syllables_list = []
for token in tokens:
    i=0
    if token == '$':
        continue
    while i < len(token):
        if token[i] in vyanjans:
            string = PurnaVyanjan(token,i)
            syllables_list.append(string)
            i = i + len(string)-1
        elif token[i] in swars:
            syllables_list.append(token[i])
        i += 1

In [97]:
syllables_dict = Counter(syllables_list)
freq_words_syllables = heapq.nlargest(len(syllables_dict.keys()), syllables_dict, key = syllables_dict.get)
print("Top 20 Syllables with frequency")
for i in freq_words_syllables[0:20]:
    print(i,syllables_dict[i])

Top 20 Syllables with frequency
ર 559267
ક 352247
મા 269604
પ 259790
સ 250668
ન 239591
ત 221641
મ 198376
વા 190246
વ 180567
ને 170736
ના 167544
આ 164370
અ 150064
છે 143520
લ 131051
ય 126488
ટ 124651
જ 124407
ની 122709


In [98]:
print(len(syllables_list))

9101137


## **Bigram output**

In [99]:
def bigram(tokens):
    bi_dict = defaultdict(int)
    for i in range(len(tokens)-1):
        if tokens[i] == '$' or tokens[i+1] == '$':  # to check that the last word of a sentence should not link with first word of next sentence.
            continue
        else:
            bi_dict[tokens[i]+" "+tokens[i+1]] += 1
    
    freq_words = heapq.nlargest(20, bi_dict, key=bi_dict.get)
    
    print("Top 20 bigram frquency of tokens")
    for i in freq_words[:20]:
        print(f"[{i} , {bi_dict[i]}]")

    bi_dict = defaultdict(int)
    for i in range(len(char_list)-1):
        if char_list[i] == '$' or char_list[i+1] == '$':  # to check that the last word of a sentence should not link with first word of next sentence.
            continue
        else:
            bi_dict[char_list[i]+" "+char_list[i+1]] += 1
    
    freq_words = heapq.nlargest(20, bi_dict, key=bi_dict.get)

    print("Top 20 bigram frquency of characters")
    for i in freq_words[:20]:
        print(f"[{i} , {bi_dict[i]}]")

    bi_dict = defaultdict(int)
    for i in range(len(syllables_list)-1):
        if syllables_list[i] == '$' or syllables_list[i+1] == '$':  # to check that the last word of a sentence should not link with first word of next sentence.
            continue
        else:
            bi_dict[syllables_list[i]+" "+syllables_list[i+1]] += 1
    freq_words = heapq.nlargest(20, bi_dict, key=bi_dict.get)
    print("Top 20 bigram frquency of syllables")
    for i in freq_words:
        print("[" + i + "," + str(bi_dict[i]) + "]")
    # print(freq_words[:20])

Get bigram Frequency of tokens

In [100]:
bi_dict = defaultdict(int)
for i in range(len(tokens)-1):
    if tokens[i] == '$' or tokens[i+1] == '$':  # to check that the last word of a sentence should not link with first word of next sentence.
        continue
    else:
        bi_dict[tokens[i]+" "+tokens[i+1]] += 1

freq_words = heapq.nlargest(20, bi_dict, key=bi_dict.get)

In [101]:
print("Top 20 bigram frquency of tokens")
for i in freq_words[:20]:
    print(f"[{i} , {bi_dict[i]}]")

Top 20 bigram frquency of tokens
[છે કે , 10130]
[છે અને , 7087]
[આવે છે , 6572]
[શકે છે , 5915]
[કરે છે , 5788]
[હોય છે , 4332]
[થાય છે , 4104]
[કરવા માટે , 3986]
[રહી છે , 3594]
[કરી હતી , 3176]
[કરવામાં આવી , 2803]
[શકો છો , 2616]
[રહ્યા છે , 2536]
[કેવી રીતે , 2518]
[આવી હતી , 2327]
[આવી છે , 2323]
[જાય છે , 2160]
[કરવામાં આવે , 2054]
[કરી છે , 2051]
[હતું કે , 2031]


Get bigram Frequency of characters from tokens

In [102]:
bi_dict = defaultdict(int)
for i in range(len(char_list)-1):
    if char_list[i] == '$' or char_list[i+1] == '$':  # to check that the last word of a sentence should not link with first word of next sentence.
        continue
    else:
        bi_dict[char_list[i]+" "+char_list[i+1]] += 1

freq_words = heapq.nlargest(20, bi_dict, key=bi_dict.get)

In [103]:
print("Top 20 bigram frquency of characters")
for i in freq_words[:20]:
    print(f"[{i} , {bi_dict[i]}]")

Top 20 bigram frquency of characters
[ર् અ , 436971]
[અ ર् , 430384]
[અ ન् , 380435]
[ક् અ , 280689]
[મ् આ , 269624]
[અ મ् , 249097]
[અ ક् , 233427]
[આ ર् , 229180]
[અ ત् , 210869]
[અ વ् , 207338]
[પ् અ , 191521]
[વ् આ , 190251]
[મ् અ , 186803]
[ન् અ , 178216]
[ન् એ , 170793]
[ન् આ , 167588]
[સ् અ , 164244]
[આ ન् , 153337]
[વ् અ , 151226]
[ત् અ , 150957]


Get bigram Frequency of syllables from tokens

In [104]:
bi_dict = defaultdict(int)
for i in range(len(syllables_list)-1):
    if syllables_list[i] == '$' or syllables_list[i+1] == '$':  # to check that the last word of a sentence should not link with first word of next sentence.
        continue
    else:
        bi_dict[syllables_list[i]+" "+syllables_list[i+1]] += 1
freq_words = heapq.nlargest(20, bi_dict, key=bi_dict.get)

In [105]:
print("Top 20 bigram frquency of syllables")
for i in freq_words:
    print("[" + i + "," + str(bi_dict[i]) + "]")
# print(freq_words[:20])

Top 20 bigram frquency of syllables
[પ ર,71853]
[ક ર,65151]
[અ ને,63661]
[વા મા,42150]
[ર વા,37006]
[મા ટે,35385]
[એ ક,32502]
[કા ર,30878]
[મા આ,30199]
[પ ણ,30187]
[ક રી,29487]
[ત ર,28615]
[વ ર,25047]
[ર ક,22385]
[ર મા,22209]
[દ ર,21422]
[સ ર,20739]
[આ વ,20363]
[સા થે,20357]
[ર ણ,19486]


# **Question 3 pdf is attached with the submission**

# **Question 4**

In [106]:
# Read file and store it the gujarati_corpus
#Given file will be used to perform serveral tokenization models
try:
    with open('gu_100.txt', 'r', encoding='utf-8') as file:
        gujarati_corpus = file.readlines()
except UnicodeDecodeError:
    print("Error: Unable to decode file with UTF-8 encoding. Trying different encoding...")
    with open('gu_100.txt', 'r', encoding='latin-1') as file:
        gujarati_corpus = file.readlines()

In [107]:
# Function arg=(list of list), and returns a signle list
def flatten_list(list_of_lists):
    flattened_list = []
    for sublist in list_of_lists:
        flattened_list.extend(sublist)
    return flattened_list

### **Unigram Freq of tokens, char, syllabals**

In [108]:
# Functions creates a list containing tokens and there frequency
# Argument passed = List of tokens
# Prints Tokens with their frequency in descending order
def freqToken(tokens):
    token_counter = Counter(tokens)

  # Sort tokens by frequency in descending order
    sorted_tokens = sorted(token_counter.items(), key=lambda x: x[1], reverse=True)

    # Print sorted tokens
    print("Tokens with their frequency")
    for token, freq in sorted_tokens:
        print(f"({token}, {freq})", end="  ")

In [109]:
# Functions creates a list containing char and there frequency
# Argument passed = List of tokens
# Prints characters with their frequency in descending order
def freqChar(tokenized_corpus):
  # for tokenized_corpus in tokens:
    char_list = []
    for i in tokenized_corpus:
        for j in unicode(i).split():   #unicode_correction of tokens and counting characters.Unicode(i) will return corrected word.
            char_list.append(j)
    char_dict_bpe = Counter(char_list)
    freq_char_bpe = heapq.nlargest(len(char_dict_bpe.keys()), char_dict_bpe, key = char_dict_bpe.get)  # freq_chars will store the character with decreasing order of their frequency.
    print("Characters with their frequency")
    for i in freq_char_bpe:
      print(f"({i}, {char_dict_bpe[i]})", end="  ")
        # print(i,char_dict_bpe[i])

In [110]:
# Functions creates a list containing syllables and there frequency
# Argument passed = List of tokens
# Prints syllables with their frequency in descending order
def freqSyllable(tokenized_corpus):
  # for tokenized_corpus in tokens:
    syllables_list = []
    for token in tokenized_corpus:
        i=0
        while i < len(token):
            if token[i] in vyanjans:
                string = PurnaVyanjan(token,i)   # calling purnavyanjan function.
                syllables_list.append(string)
                i = i + len(string)-1
            elif token[i] in swars:
                syllables_list.append(token[i])
            i += 1
    syllables_dict_bpe = Counter(syllables_list)

    freq_syllable_bpe = heapq.nlargest(len(syllables_dict_bpe.keys()), syllables_dict_bpe, key = syllables_dict_bpe.get) # freq_syllables_bpe will store the syllables with decreasing order of their frequency.
    print("Syllables with their frequency")
    for i in freq_syllable_bpe:
      print(f"({i}, {syllables_dict_bpe[i]})", end="  ")
        # print(i,syllables_dict_bpe[i])

# **(1) mBERT**

In [111]:
# Initialize the mBERT tokenizer
def mBERT_Model(gujarati_corpus,length):
  mBERT_tokenizer = BertTokenizer.from_pretrained('bert-base-multilingual-cased')

  # Tokenize each line of the corpus
  tokenized_corpus = []

  for line in gujarati_corpus:
      # Tokenize the text with maximum length specified
      encoding = mBERT_tokenizer.encode_plus(line.strip(), max_length=length, truncation=True, return_tensors='pt')

      # Decode the tokens to remove subword prefixes '#' and reconstruct the original text
      decoded_tokens = mBERT_tokenizer.convert_ids_to_tokens(encoding['input_ids'].squeeze())
      decoded_text = mBERT_tokenizer.decode(encoding['input_ids'].squeeze(), skip_special_tokens=True)

      # Remove '#' symbols from the tokens
      cleaned_tokens = [remove_trivial_prefix_suffix(token) for token in decoded_tokens]
      # remove_trivial_prefix_suffix(cleaned_tokens)

      # Remove empty tokens
      cleaned_tokens = [token for token in cleaned_tokens if token]

      # Join the cleaned tokens back to text
      # cleaned_text = ' '.join(cleaned_tokens)

      tokenized_corpus.append(cleaned_tokens)
      # print(tokenized_corpus)
  return tokenized_corpus




In [112]:
# For max length 1k
mbert1k = mBERT_Model(gujarati_corpus,1000)
# print(mbert1k)
mbert1k = flatten_list(mbert1k)
# print(mbert1k)

Printing Frequencies of tokens, characters, syllables

In [113]:
freqToken(mbert1k)

Tokens with their frequency
(ર, 1524305)  (ન, 1355315)  (મ, 1054070)  (ક, 1037534)  (ત, 873779)  (સ, 853942)  (વ, 808708)  (પ, 663973)  (લ, 633935)  (ય, 580727)  (જ, 549544)  (CLS, 442127)  (SEP, 442127)  (છ, 396523)  (હ, 380641)  (દ, 376218)  (ગ, 356897)  (બ, 354120)  (ટ, 352525)  (શ, 319665)  (ડ, 305618)  (આ, 267229)  (ચ, 223284)  (થ, 222118)  (ણ, 200327)  (ધ, 186192)  (ખ, 171151)  (અ, 170753)  (એ, 169910)  (અન, 156253)  (ભ, 155981)  (ળ, 155736)  (ફ, 144046)  (ઓ, 115299)  (ઈ, 110569)  (કર, 101085)  (ઇ, 100957)  (હત, 97620)  (મટ, 90702)  (પર, 86379)  (ષ, 81449)  (ઉ, 81268)  (એક, 76267)  (ઘ, 54316)  (પણ, 53833)  (સથ, 53816)  (ઝ, 50145)  (વર, 48363)  (આવ, 43389)  (ઠ, 40426)  (તન, 35488)  (કરવ, 34746)  (નથ, 30431)  (નટ, 28294)  (વમ, 27887)  (UNK, 26288)  (સટ, 25574)  (રણ, 24972)  (તમન, 24426)  (હય, 22614)  (૦, 21815)  (૧, 20790)  (શન, 20592)  (કરવમ, 20578)  (વધ, 19804)  (શક, 19573)  (રત, 19029)  (થય, 18953)  (દવર, 18567)  (પરત, 18177)  (લક, 18034)  (અથવ, 17543)  (તર, 17304)  (આવય, 17153)

In [114]:
freqChar(mbert1k)

Characters with their frequency
(અ, 18550865)  (ર्, 2127570)  (ન्, 1733305)  (ક्, 1386014)  (મ्, 1324256)  (ત्, 1207197)  (વ्, 1149240)  (સ्, 976032)  (પ्, 866658)  (ય्, 744753)  (લ्, 684619)  (જ्, 584667)  (ટ्, 520359)  (હ्, 516589)  (દ्, 427292)  (છ्, 412052)  (ગ्, 396687)  (બ्, 378892)  (શ्, 374519)  (થ्, 368237)  (આ, 330992)  (ણ्, 309912)  (ડ्, 307931)  (એ, 250717)  (ધ्, 238934)  (ચ्, 224172)  (ખ्, 182696)  (ભ्, 168718)  (ળ्, 158383)  (ફ्, 150752)  (ઓ, 135992)  (ઈ, 122979)  (ષ्, 113997)  (ઇ, 100957)  (ઉ, 99566)  (ઘ्, 54582)  (ઝ्, 50145)  (ઠ्, 40426)  (ઢ्, 11654)  (ઊ, 8794)  (ઞ्, 4927)  (ઑ, 2577)  (ઔ, 1389)  (ઍ, 1270)  (ઋ, 919)  (ઐ, 913)  

In [115]:
freqSyllable(mbert1k)

Syllables with their frequency
(ર, 2127570)  (ન, 1733305)  (ક, 1385940)  (મ, 1324256)  (ત, 1193284)  (વ, 1149240)  (સ, 976032)  (પ, 866658)  (ય, 744753)  (લ, 684619)  (જ, 584667)  (ટ, 520359)  (હ, 516589)  (દ, 427292)  (છ, 412052)  (ગ, 396687)  (બ, 378892)  (શ, 374519)  (થ, 355827)  (અ, 354698)  (આ, 330992)  (ણ, 309912)  (ડ, 307931)  (એ, 250717)  (ધ, 238934)  (ચ, 224172)  (ખ, 182696)  (ભ, 168718)  (ળ, 158383)  (ફ, 150752)  (ઓ, 122005)  (ષ, 113997)  (ઈ, 110569)  (ઇ, 100957)  (ઉ, 99302)  (ઘ, 54318)  (ઝ, 50145)  (ઠ, 40426)  (તઓ, 13913)  (થઈ, 12410)  (ઢ, 11654)  (ઊ, 8794)  (ઞ, 4927)  (ઑ, 2577)  (ઔ, 1389)  (ઍ, 1270)  (ઋ, 919)  (ઐ, 913)  (ઘઉ, 264)  (કઓ, 74)  

In [116]:
bigram(mbert1k)

Top 20 bigram frquency of tokens
[SEP CLS , 442126]
[છ SEP , 188494]
[પ ર , 181723]
[ક ર , 172657]
[ર મ , 117828]
[ન સ , 108761]
[ત મ , 106152]
[મ ર , 101300]
[ત ર , 98533]
[ર ક , 97884]
[સ મ , 97463]
[ર ન , 96053]
[ન ક , 88828]
[મ ન , 85918]
[સ ર , 83616]
[ન ન , 83427]
[દ ર , 83391]
[ત ન , 82118]
[ન વ , 81446]
[ન મ , 79593]
Top 20 bigram frquency of characters
[ર् અ , 436971]
[અ ર् , 430384]
[અ ન् , 380435]
[ક् અ , 280689]
[મ् આ , 269624]
[અ મ् , 249097]
[અ ક् , 233427]
[આ ર् , 229180]
[અ ત् , 210869]
[અ વ् , 207338]
[પ् અ , 191521]
[વ् આ , 190251]
[મ् અ , 186803]
[ન् અ , 178216]
[ન् એ , 170793]
[ન् આ , 167588]
[સ् અ , 164244]
[આ ન् , 153337]
[વ् અ , 151226]
[ત् અ , 150957]
Top 20 bigram frquency of syllables
[પ ર,71853]
[ક ર,65151]
[અ ને,63661]
[વા મા,42150]
[ર વા,37006]
[મા ટે,35385]
[એ ક,32502]
[કા ર,30878]
[મા આ,30199]
[પ ણ,30187]
[ક રી,29487]
[ત ર,28615]
[વ ર,25047]
[ર ક,22385]
[ર મા,22209]
[દ ર,21422]
[સ ર,20739]
[આ વ,20363]
[સા થે,20357]
[ર ણ,19486]


mBert max length 2k

In [117]:
# mBert max length 2k
mbert2k = mBERT_Model(gujarati_corpus,2000)
mbert2k = flatten_list(mbert2k)

Printing Frequencies of tokens, characters, syllables

In [118]:
freqToken(mbert2k)

Tokens with their frequency
(ર, 1524912)  (ન, 1355858)  (મ, 1054493)  (ક, 1037902)  (ત, 874141)  (સ, 854293)  (વ, 809086)  (પ, 664242)  (લ, 634172)  (ય, 580978)  (જ, 549808)  (CLS, 442127)  (SEP, 442127)  (છ, 396659)  (હ, 380854)  (દ, 376377)  (ગ, 357051)  (બ, 354247)  (ટ, 352641)  (શ, 319816)  (ડ, 305706)  (આ, 267334)  (ચ, 223377)  (થ, 222222)  (ણ, 200406)  (ધ, 186276)  (ખ, 171219)  (અ, 170825)  (એ, 170018)  (અન, 156298)  (ભ, 156068)  (ળ, 155796)  (ફ, 144073)  (ઓ, 115336)  (ઈ, 110623)  (કર, 101108)  (ઇ, 101006)  (હત, 97658)  (મટ, 90724)  (પર, 86401)  (ષ, 81481)  (ઉ, 81300)  (એક, 76282)  (ઘ, 54329)  (પણ, 53867)  (સથ, 53827)  (ઝ, 50157)  (વર, 48373)  (આવ, 43403)  (ઠ, 40436)  (તન, 35496)  (કરવ, 34755)  (નથ, 30447)  (નટ, 28298)  (વમ, 27893)  (UNK, 26315)  (સટ, 25577)  (રણ, 24979)  (તમન, 24434)  (હય, 22624)  (૦, 21825)  (૧, 20796)  (શન, 20604)  (કરવમ, 20582)  (વધ, 19807)  (શક, 19579)  (રત, 19035)  (થય, 18961)  (દવર, 18572)  (પરત, 18178)  (લક, 18041)  (અથવ, 17547)  (તર, 17307)  (આવય, 17158)

In [119]:
freqChar(mbert2k)

Characters with their frequency
(અ, 18557931)  (ર्, 2128329)  (ન्, 1733970)  (ક्, 1386467)  (મ्, 1324748)  (ત्, 1207674)  (વ्, 1149696)  (સ्, 976410)  (પ्, 866997)  (ય्, 745067)  (લ्, 684870)  (જ्, 584941)  (ટ्, 520506)  (હ्, 516853)  (દ्, 427464)  (છ्, 412191)  (ગ्, 396856)  (બ्, 379025)  (શ्, 374692)  (થ्, 368389)  (આ, 331118)  (ણ्, 310036)  (ડ्, 308019)  (એ, 250841)  (ધ्, 239034)  (ચ्, 224265)  (ખ्, 182767)  (ભ्, 168809)  (ળ्, 158443)  (ફ्, 150781)  (ઓ, 136035)  (ઈ, 123038)  (ષ्, 114033)  (ઇ, 101006)  (ઉ, 99604)  (ઘ्, 54595)  (ઝ्, 50157)  (ઠ्, 40436)  (ઢ्, 11656)  (ઊ, 8796)  (ઞ्, 4933)  (ઑ, 2577)  (ઔ, 1389)  (ઍ, 1270)  (ઋ, 919)  (ઐ, 913)  

In [120]:
freqSyllable(mbert2k)

Syllables with their frequency
(ર, 2128329)  (ન, 1733970)  (ક, 1386393)  (મ, 1324748)  (ત, 1193757)  (વ, 1149696)  (સ, 976410)  (પ, 866997)  (ય, 745067)  (લ, 684870)  (જ, 584941)  (ટ, 520506)  (હ, 516853)  (દ, 427464)  (છ, 412191)  (ગ, 396856)  (બ, 379025)  (શ, 374692)  (થ, 355974)  (અ, 354822)  (આ, 331118)  (ણ, 310036)  (ડ, 308019)  (એ, 250841)  (ધ, 239034)  (ચ, 224265)  (ખ, 182767)  (ભ, 168809)  (ળ, 158443)  (ફ, 150781)  (ઓ, 122044)  (ષ, 114033)  (ઈ, 110623)  (ઇ, 101006)  (ઉ, 99340)  (ઘ, 54331)  (ઝ, 50157)  (ઠ, 40436)  (તઓ, 13917)  (થઈ, 12415)  (ઢ, 11656)  (ઊ, 8796)  (ઞ, 4933)  (ઑ, 2577)  (ઔ, 1389)  (ઍ, 1270)  (ઋ, 919)  (ઐ, 913)  (ઘઉ, 264)  (કઓ, 74)  

In [121]:
bigram(mbert2k)

Top 20 bigram frquency of tokens
[SEP CLS , 442126]
[છ SEP , 188502]
[પ ર , 181797]
[ક ર , 172719]
[ર મ , 117873]
[ન સ , 108806]
[ત મ , 106187]
[મ ર , 101335]
[ત ર , 98579]
[ર ક , 97926]
[સ મ , 97493]
[ર ન , 96069]
[ન ક , 88857]
[મ ન , 85981]
[સ ર , 83651]
[ન ન , 83460]
[દ ર , 83416]
[ત ન , 82162]
[ન વ , 81485]
[ન મ , 79631]
Top 20 bigram frquency of characters
[ર् અ , 436971]
[અ ર् , 430384]
[અ ન् , 380435]
[ક् અ , 280689]
[મ् આ , 269624]
[અ મ् , 249097]
[અ ક् , 233427]
[આ ર् , 229180]
[અ ત् , 210869]
[અ વ् , 207338]
[પ् અ , 191521]
[વ् આ , 190251]
[મ् અ , 186803]
[ન् અ , 178216]
[ન् એ , 170793]
[ન् આ , 167588]
[સ् અ , 164244]
[આ ન् , 153337]
[વ् અ , 151226]
[ત् અ , 150957]
Top 20 bigram frquency of syllables
[પ ર,71853]
[ક ર,65151]
[અ ને,63661]
[વા મા,42150]
[ર વા,37006]
[મા ટે,35385]
[એ ક,32502]
[કા ર,30878]
[મા આ,30199]
[પ ણ,30187]
[ક રી,29487]
[ત ર,28615]
[વ ર,25047]
[ર ક,22385]
[ર મા,22209]
[દ ર,21422]
[સ ર,20739]
[આ વ,20363]
[સા થે,20357]
[ર ણ,19486]


# **(2) Indic_BERT**

I have attached a saparate file named (Assignment_1_Indic_BERT_Model.ipynb)containing the same code given below for Indic_BERT as it was not working here properly

In [122]:
# def IndicBert_Model(gujarati_corpus,length):
#   IndicBERT_tokenizer = AutoTokenizer.from_pretrained('ai4bharat/indic-bert', keep_accents=True,max_length = length)
#   tokenized_corpus = []
#   for line in gujarati_corpus:
#           cleaned_tokens = []
#           tokens = IndicBERT_tokenizer.tokenize(line.strip())
#           cleaned_tokens = [remove_trivial_prefix_suffix(token) for token in tokens]
#           # for token in cleaned_tokens:
#           tokenized_corpus.append(cleaned_tokens)
# #   print(tokenized_corpus)
#   return tokenized_corpus

In [123]:
# indicbert1k = flatten_list(IndicBert_Model(gujarati_corpus,1000))
# indicbert1k

In [124]:
# freqToken(indicbert1k)

In [125]:
# freqChar(indicbert1k)


In [126]:
# freqSyllable(indicbert1k)

In [127]:
# indicbert2k = flatten_list(IndicBert_Model(gujarati_corpus,2000))

In [128]:
# freqToken(indicbert2k)


In [129]:
# freqChar(indicbert2k)


In [130]:
# freqSyllable(indicbert2k)

# **BPE**

In [131]:
def BPE_Model(gujarati_corpus, length):
  input_data_path = "gu_100.txt"

  spm.SentencePieceTrainer.train(input=input_data_path, model_prefix='bpe_model', vocab_size=length,model_type='bpe')


  tokenizer_1k = spm.SentencePieceProcessor(model_file='bpe_model.model')

  tokenized_corpus_1k = []

  for line in gujarati_corpus:
    tokens = tokenizer_1k.encode(line, out_type=str)
    cleaned_tokens = [remove_trivial_prefix_suffix(token) for token in tokens]
    # for token in tokens:
    tokenized_corpus_1k.append(cleaned_tokens)
  return tokenized_corpus_1k


In [132]:
bpemodel1k = flatten_list(BPE_Model(gujarati_corpus,1000))

In [133]:
freqToken(bpemodel1k)


Tokens with their frequency
(, 1745712)  (ન, 1055881)  (ર, 803906)  (મ, 702096)  (ક, 676880)  (ત, 594064)  (વ, 557448)  (લ, 541402)  (સ, 535249)  (ય, 416096)  (જ, 394848)  (છ, 388295)  (પ, 340335)  (ટ, 271261)  (બ, 255168)  (ડ, 252152)  (ગ, 249158)  (દ, 243790)  (શ, 229622)  (હ, 206119)  (પર, 186279)  (ચ, 179012)  (કર, 170709)  (આ, 170013)  (અન, 169758)  (એ, 152074)  (થ, 148805)  (ણ, 143560)  (ખ, 127088)  (ળ, 114061)  (ભ, 113490)  (ધ, 112194)  (ફ, 110788)  (હત, 107360)  (ઓ, 93319)  (મટ, 90537)  (અ, 89230)  (ઇ, 86065)  (સથ, 81271)  (એક, 70724)  (ઈ, 69287)  (પણ, 68073)  (આવ, 66418)  (તર, 54793)  (ઉ, 52348)  (વર, 51261)  (સમ, 50373)  (ઝ, 45591)  (1, 38968)  (ઘ, 38626)  (કષ, 38494)  (શક, 37999)  (વધ, 37195)  (સટ, 37064)  (આપ, 36480)  (રહ, 36294)  (તમ, 35922)  (તન, 35383)  (દર, 34813)  (સર, 34582)  (ગર, 33074)  (વન, 32898)  (વમ, 31049)  (તમન, 30992)  (ઠ, 30647)  (નથ, 30440)  (મળ, 29264)  (કરય, 28673)  (ષ, 28514)  (કરવ, 28391)  (લક, 27207)  (રત, 26811)  (2, 25645)  (બન, 25603)  (પરત, 23877) 

In [134]:
freqChar(bpemodel1k)


Characters with their frequency
(અ, 18559599)  (ર्, 2128526)  (ન्, 1734112)  (ક्, 1386555)  (મ्, 1324843)  (ત्, 1207724)  (વ्, 1149790)  (સ्, 976491)  (પ्, 867048)  (ય्, 745130)  (લ्, 684911)  (જ्, 585042)  (ટ्, 520557)  (હ्, 516880)  (દ्, 427491)  (છ्, 412209)  (ગ्, 396930)  (બ्, 379101)  (શ्, 374717)  (થ्, 368405)  (આ, 331134)  (ણ्, 310058)  (ડ्, 308070)  (એ, 250862)  (ધ्, 239054)  (ચ्, 224280)  (ખ्, 182786)  (ભ्, 168822)  (ળ्, 158447)  (ફ्, 150791)  (ઓ, 136048)  (ઈ, 123055)  (ષ्, 114074)  (ઇ, 101041)  (ઉ, 99613)  (ઘ्, 54607)  (ઝ्, 50170)  (ઠ्, 40439)  (ઢ्, 11663)  (ઊ, 8797)  (ઞ्, 4933)  (ઑ, 2580)  (ઔ, 1389)  (ઍ, 1271)  (ઋ, 919)  (ઐ, 913)  (ઙ्, 113)  

In [135]:
freqSyllable(bpemodel1k)

Syllables with their frequency
(ર, 2128526)  (ન, 1734112)  (ક, 1364677)  (મ, 1324843)  (ત, 1189643)  (વ, 1149790)  (સ, 976491)  (પ, 867048)  (ય, 745130)  (લ, 678820)  (જ, 573226)  (ટ, 520557)  (હ, 516880)  (દ, 427491)  (છ, 412209)  (ગ, 396930)  (બ, 379101)  (શ, 374717)  (અ, 354831)  (થ, 349845)  (આ, 331134)  (ણ, 310058)  (ડ, 308070)  (એ, 250862)  (ધ, 239054)  (ચ, 224280)  (ખ, 182786)  (ભ, 162836)  (ળ, 158447)  (ફ, 150791)  (ઓ, 117967)  (ષ, 114074)  (ઉ, 99613)  (ઇ, 90478)  (ઈ, 69287)  (ઘ, 54607)  (ઝ, 50170)  (ઠ, 40439)  (તઓ, 18081)  (કઈ, 17463)  (થઈ, 12412)  (જઈ, 11816)  (ઢ, 11663)  (ઊ, 8797)  (થઇ, 6148)  (લઈ, 6091)  (ભઈ, 5986)  (ઞ, 4933)  (કઇ, 4415)  (ઑ, 2580)  (ઔ, 1389)  (ઍ, 1271)  (ઋ, 919)  (ઐ, 913)  (ઙ, 113)  

In [136]:
bigram(bpemodel1k)

Top 20 bigram frquency of tokens
[છ  , 261657]
[  , 132865]
[હત  , 79357]
[ મ , 74475]
[ ત , 72848]
[ જ , 70920]
[ ન , 66854]
[ ક , 60534]
[ક  , 60244]
[ સ , 58757]
[ આ , 55078]
[મ ન , 53252]
[ન ન , 51016]
[ર ન , 49221]
[ન સ , 49066]
[ત ન , 48695]
[ન મ , 47653]
[ર  , 47253]
[ન ક , 46934]
[ર મ , 46841]
Top 20 bigram frquency of characters
[ર् અ , 436971]
[અ ર् , 430384]
[અ ન् , 380435]
[ક् અ , 280689]
[મ् આ , 269624]
[અ મ् , 249097]
[અ ક् , 233427]
[આ ર् , 229180]
[અ ત् , 210869]
[અ વ् , 207338]
[પ् અ , 191521]
[વ् આ , 190251]
[મ् અ , 186803]
[ન् અ , 178216]
[ન् એ , 170793]
[ન् આ , 167588]
[સ् અ , 164244]
[આ ન् , 153337]
[વ् અ , 151226]
[ત् અ , 150957]
Top 20 bigram frquency of syllables
[પ ર,71853]
[ક ર,65151]
[અ ને,63661]
[વા મા,42150]
[ર વા,37006]
[મા ટે,35385]
[એ ક,32502]
[કા ર,30878]
[મા આ,30199]
[પ ણ,30187]
[ક રી,29487]
[ત ર,28615]
[વ ર,25047]
[ર ક,22385]
[ર મા,22209]
[દ ર,21422]
[સ ર,20739]
[આ વ,20363]
[સા થે,20357]
[ર ણ,19486]


In [137]:
bpemodel2k = flatten_list(BPE_Model(gujarati_corpus,2000))

In [138]:
freqToken(bpemodel2k)


Tokens with their frequency
(, 1340199)  (ન, 807344)  (ર, 488436)  (ક, 484073)  (મ, 481434)  (ત, 432034)  (લ, 376447)  (છ, 365288)  (સ, 365143)  (વ, 356172)  (જ, 294284)  (ય, 278695)  (પ, 227485)  (ડ, 200538)  (ટ, 197690)  (બ, 186124)  (ગ, 180473)  (અન, 163358)  (દ, 160939)  (શ, 160724)  (પર, 147761)  (કર, 145544)  (હ, 137361)  (આ, 131427)  (થ, 116317)  (ચ, 108783)  (એ, 105662)  (હત, 101926)  (ણ, 95739)  (મટ, 94363)  (ફ, 94100)  (ખ, 80197)  (ભ, 76779)  (ધ, 76740)  (ળ, 76085)  (એક, 72314)  (સથ, 71735)  (ઓ, 69531)  (પણ, 67043)  (અ, 60701)  (આવ, 59657)  (ઇ, 53202)  (ઈ, 47275)  (તર, 45493)  (વર, 44315)  (તન, 43743)  (વન, 43594)  (તમ, 41634)  (ઝ, 40144)  (સટ, 38990)  (મન, 37324)  (દર, 37027)  (શક, 37024)  (સમ, 33704)  (ઉ, 32886)  (કરવ, 31355)  (તમન, 30992)  (નથ, 30440)  (થય, 30170)  (સર, 29692)  (કષ, 28994)  (આપ, 28780)  (ઘ, 28580)  (રહ, 27521)  (વધ, 27083)  (રમ, 25954)  (ઠ, 25879)  (બન, 25766)  (મળ, 25515)  (રત, 25473)  (1, 25230)  (ગર, 24643)  (કરય, 23908)  (પરત, 23877)  (ટર, 22733)  (હય,

In [139]:
freqChar(bpemodel2k)


Characters with their frequency
(અ, 18559599)  (ર्, 2128526)  (ન्, 1734112)  (ક्, 1386555)  (મ्, 1324843)  (ત्, 1207724)  (વ्, 1149790)  (સ्, 976491)  (પ्, 867048)  (ય्, 745130)  (લ्, 684911)  (જ्, 585042)  (ટ्, 520557)  (હ्, 516880)  (દ्, 427491)  (છ्, 412209)  (ગ्, 396930)  (બ्, 379101)  (શ्, 374717)  (થ्, 368405)  (આ, 331134)  (ણ्, 310058)  (ડ्, 308070)  (એ, 250862)  (ધ्, 239054)  (ચ्, 224280)  (ખ्, 182786)  (ભ्, 168822)  (ળ्, 158447)  (ફ्, 150791)  (ઓ, 136048)  (ઈ, 123055)  (ષ्, 114074)  (ઇ, 101041)  (ઉ, 99613)  (ઘ्, 54607)  (ઝ्, 50170)  (ઠ्, 40439)  (ઢ्, 11663)  (ઊ, 8797)  (ઞ्, 4933)  (ઑ, 2580)  (ઔ, 1389)  (ઍ, 1271)  (ઋ, 919)  (ઐ, 913)  (ઙ्, 113)  

In [140]:
freqSyllable(bpemodel2k)

Syllables with their frequency
(ર, 2120354)  (ન, 1734112)  (ક, 1362336)  (મ, 1324843)  (ત, 1189643)  (વ, 1149790)  (સ, 976491)  (પ, 867048)  (ય, 745130)  (લ, 672473)  (જ, 566207)  (ટ, 520557)  (હ, 511750)  (દ, 427491)  (છ, 408507)  (ગ, 391083)  (બ, 377394)  (શ, 374717)  (અ, 354831)  (થ, 349845)  (આ, 328457)  (ણ, 310058)  (ડ, 308070)  (એ, 245501)  (ધ, 239054)  (ચ, 224280)  (ખ, 182786)  (ભ, 159388)  (ળ, 158447)  (ફ, 150791)  (ષ, 114074)  (ઓ, 112500)  (ઉ, 97374)  (ઇ, 80368)  (ઘ, 54607)  (ઈ, 51428)  (ઝ, 50170)  (ઠ, 40439)  (કઈ, 19804)  (તઓ, 18081)  (જઈ, 13930)  (થઈ, 12412)  (ઢ, 11663)  (લઈ, 9050)  (ઊ, 8797)  (થઇ, 6148)  (ભઈ, 5986)  (હઈ, 5130)  (ઞ, 4933)  (કઇ, 4415)  (રઓ, 3836)  (છએ, 3702)  (ગઈ, 3608)  (ભઇ, 3448)  (લઇ, 3388)  (જઇ, 3274)  (રઆ, 2677)  (ઑ, 2580)  (ગઉ, 2239)  (બઈ, 1707)  (રએ, 1659)  (જઓ, 1631)  (ઔ, 1389)  (ઍ, 1271)  (ઋ, 919)  (ઐ, 913)  (ઙ, 113)  

In [141]:
bigram(bpemodel2k)

Top 20 bigram frquency of tokens
[છ  , 255835]
[  , 83623]
[હત  , 74379]
[ આ , 46219]
[ જ , 46060]
[ ત , 46051]
[ ન , 40643]
[ સ , 39417]
[ક  , 38329]
[ ક , 37670]
[ મ , 37096]
[ક ન , 31818]
[ર ન , 31258]
[ત  , 28862]
[ પ , 28032]
[ય  , 27840]
[ત ન , 27701]
[ન ન , 27636]
[ન  , 27435]
[ર  , 27320]
Top 20 bigram frquency of characters
[ર् અ , 436971]
[અ ર् , 430384]
[અ ન् , 380435]
[ક् અ , 280689]
[મ् આ , 269624]
[અ મ् , 249097]
[અ ક् , 233427]
[આ ર् , 229180]
[અ ત् , 210869]
[અ વ् , 207338]
[પ् અ , 191521]
[વ् આ , 190251]
[મ् અ , 186803]
[ન् અ , 178216]
[ન् એ , 170793]
[ન् આ , 167588]
[સ् અ , 164244]
[આ ન् , 153337]
[વ् અ , 151226]
[ત् અ , 150957]
Top 20 bigram frquency of syllables
[પ ર,71853]
[ક ર,65151]
[અ ને,63661]
[વા મા,42150]
[ર વા,37006]
[મા ટે,35385]
[એ ક,32502]
[કા ર,30878]
[મા આ,30199]
[પ ણ,30187]
[ક રી,29487]
[ત ર,28615]
[વ ર,25047]
[ર ક,22385]
[ર મા,22209]
[દ ર,21422]
[સ ર,20739]
[આ વ,20363]
[સા થે,20357]
[ર ણ,19486]


# **UNIGRAM**

In [142]:
def UNIGRAM_MODEL(gujarati_corpus):
  model_prefix = "unigram_model"

  spm.SentencePieceTrainer.train(input='gu_100.txt', model_prefix=model_prefix, model_type='unigram',vocab_size=300)
  tokenizer = spm.SentencePieceProcessor(model_file= "unigram_model.model")
  tokenized_corpus_2k = []

  for line in gujarati_corpus:
    tokens = tokenizer.encode(line, out_type=str)
    cleaned_tokens = [token.lstrip('▁') for token in tokens]
    # for token in tokens:
    tokenized_corpus_2k.append(cleaned_tokens)
  return tokenized_corpus_2k


  # for tokens in tokenized_corpus_2k:
  #     print(tokens)

In [143]:
unigramModelData = flatten_list(UNIGRAM_MODEL(gujarati_corpus))

In [144]:
freqToken(unigramModelData)


Tokens with their frequency
(ર, 818404)  (ા, 771021)  (ે, 760328)  (ો, 729824)  (મ, 705487)  (ી, 590149)  (સ, 579496)  (ક, 568639)  (, 553337)  (ન, 497954)  (પ, 482735)  (., 450486)  (લ, 417986)  (ત, 417591)  (જ, 414399)  (વ, 413363)  (બ, 363145)  (િ, 360678)  (ં, 355378)  (હ, 327484)  (દ, 323399)  (ના, 321443)  (છે, 320962)  (ગ, 314340)  (્, 307319)  (ટ, 293706)  (ુ, 267885)  (વા, 267254)  (આ, 261957)  (,, 260111)  (માં, 249551)  (ડ, 246542)  (ની, 243354)  (શ, 240878)  (ને, 214612)  (ણ, 193012)  (ર્, 191639)  (ચ, 190762)  (અ, 181847)  (ૂ, 177100)  (તે, 176940)  (એ, 176835)  (મા, 174134)  (્ર, 171788)  (ખ, 169683)  (ધ, 165639)  (ળ, 158447)  (અને, 155795)  (ફ, 150791)  (તા, 141844)  (લા, 139546)  (થ, 136677)  (કે, 121242)  (ભ, 121002)  (ય, 120505)  (્યા, 118857)  (રી, 109436)  (નો, 107939)  (થી, 107262)  (કર, 105858)  (ઈ, 105592)  (ઓ, 104419)  (પ્ર, 103271)  (્ય, 99345)  (કા, 91977)  (ાય, 90498)  (વિ, 89042)  (ઉ, 87407)  (માટે, 83880)  (રા, 83544)  (ું, 80384)  (પર, 79891)  (વી, 76959) 

In [145]:
freqChar(unigramModelData)

Characters with their frequency
(અ, 12170131)  (આ, 2801374)  (ર्, 2128526)  (ન्, 1734112)  (એ, 1709638)  (ક्, 1386555)  (મ्, 1324843)  (ત्, 1207724)  (વ्, 1149790)  (સ्, 976491)  (ઈ, 967714)  (પ्, 867048)  (ય्, 745130)  (લ्, 684911)  (જ्, 585042)  (ટ्, 520557)  (હ्, 516880)  (ઓ, 507026)  (દ्, 427491)  (છ्, 412209)  (ગ्, 396930)  (બ्, 379101)  (શ्, 374717)  (થ्, 368405)  (ઉ, 326250)  (ણ्, 310058)  (ડ्, 308070)  (ઇ, 267041)  (ધ्, 239054)  (ચ्, 224280)  (ખ्, 182786)  (ભ्, 168822)  (ળ्, 158447)  (ફ्, 150791)  (ષ्, 114074)  (અં, 62594)  (ઘ्, 54607)  (ઝ्, 50170)  (ઠ्, 40439)  (ઊ, 22524)  (ઢ्, 11663)  (ઞ्, 4933)  (ઑ, 2580)  (ઔ, 1389)  (ઍ, 1271)  (ઋ, 919)  (ઐ, 913)  (ઙ्, 113)  

In [146]:
freqSyllable(unigramModelData)

Syllables with their frequency
(ર, 1760285)  (ક, 1056031)  (સ, 809832)  (પ, 806332)  (મ, 722988)  (ત, 687116)  (ન, 592870)  (મા, 576012)  (વ, 494748)  (લ, 466903)  (જ, 457604)  (ટ, 436677)  (હ, 425139)  (ગ, 396930)  (વા, 393861)  (ય, 391406)  (બ, 379101)  (ને, 370407)  (દ, 355194)  (અ, 354831)  (ના, 337399)  (આ, 331134)  (શ, 321458)  (છે, 320962)  (ડ, 268360)  (ણ, 265313)  (એ, 250862)  (ની, 243354)  (યા, 221782)  (તે, 195975)  (ચ, 190762)  (થ, 185597)  (ખ, 182786)  (રી, 179430)  (ધ, 178869)  (કા, 173574)  (તા, 165223)  (ળ, 158447)  (ફ, 150791)  (રા, 145251)  (લા, 139546)  (થી, 137702)  (ઓ, 136048)  (ઈ, 123055)  (કે, 121242)  (ભ, 121002)  (ષ, 114074)  (નો, 107939)  (સા, 107821)  (ઇ, 101041)  (ઉ, 99613)  (વિ, 89042)  (ટે, 83880)  (યુ, 79263)  (વી, 76959)  (વે, 71774)  (જે, 70935)  (હે, 69122)  (પા, 60716)  (લી, 60217)  (જો, 56503)  (ઘ, 54607)  (તો, 54141)  (શે, 53259)  (યો, 52679)  (છ, 52618)  (નુ, 52300)  (ઝ, 50170)  (ભા, 47820)  (થે, 45106)  (ણી, 44745)  (સં, 44542)  (દા, 41578)  (ઠ, 4

In [147]:
bigram(unigramModelData)

Top 20 bigram frquency of tokens
[છે . , 179278]
[ર ે , 81084]
[મ ે , 77374]
[ક ો , 70943]
[ર ો , 70654]
[જ ા , 63606]
[ે છે , 62612]
[.  , 60186]
[લ ે , 59404]
[બ ા , 58433]
[ા ર , 56541]
[મ ો , 54604]
[હ ા , 50029]
[પ ો , 48841]
[સ ્ , 48612]
[જ ી , 46607]
[તે મ , 44329]
[હ ો , 42920]
[હ ી , 42590]
[ે ક , 42056]
Top 20 bigram frquency of characters
[ર् અ , 436971]
[અ ર् , 430384]
[અ ન् , 380435]
[ક् અ , 280689]
[મ् આ , 269624]
[અ મ् , 249097]
[અ ક् , 233427]
[આ ર् , 229180]
[અ ત् , 210869]
[અ વ् , 207338]
[પ् અ , 191521]
[વ् આ , 190251]
[મ् અ , 186803]
[ન् અ , 178216]
[ન् એ , 170793]
[ન् આ , 167588]
[સ् અ , 164244]
[આ ન् , 153337]
[વ् અ , 151226]
[ત् અ , 150957]
Top 20 bigram frquency of syllables
[પ ર,71853]
[ક ર,65151]
[અ ને,63661]
[વા મા,42150]
[ર વા,37006]
[મા ટે,35385]
[એ ક,32502]
[કા ર,30878]
[મા આ,30199]
[પ ણ,30187]
[ક રી,29487]
[ત ર,28615]
[વ ર,25047]
[ર ક,22385]
[ર મા,22209]
[દ ર,21422]
[સ ર,20739]
[આ વ,20363]
[સા થે,20357]
[ર ણ,19486]


# **WHITESPACE MODEL**

In [148]:
def Whitespace_Model(gujarati_corpus):
  tk = WhitespaceTokenizer()
  tokenized_corpus = []

  for line in gujarati_corpus:
          tokens = tk.tokenize(line)
          # for token in tokens:
          tokenized_corpus.append(tokens)
  return tokenized_corpus
  # for tokens in tokenized_corpus:
  #     print(tokens)

In [149]:
tokenized_corpus = flatten_list(Whitespace_Model(gujarati_corpus))

In [150]:
freqToken(tokenized_corpus)


Tokens with their frequency
(છે., 178482)  (અને, 151509)  (છે, 85214)  (આ, 78426)  (માટે, 74470)  (કે, 66147)  (એક, 58518)  (તે, 55611)  (પણ, 52790)  (પર, 46481)  (સાથે, 41610)  (છે,, 39966)  (કરી, 38986)  (જ, 37023)  (જે, 28405)  (તો, 27867)  (તમે, 25758)  (હતી., 22541)  (કરવામાં, 20525)  (આવે, 20071)  (કરવા, 19959)  (એ, 19740)  (હોય, 19228)  (દ્વારા, 17940)  (-, 17853)  (શકે, 17810)  (રીતે, 17667)  (પરંતુ, 17623)  (આવી, 17142)  (અથવા, 17073)  (કરે, 16956)  (વધુ, 16782)  (જો, 16288)  (હતો., 15042)  (., 14913)  (તેના, 14037)  (હતા., 13751)  (નથી., 13634)  (ન, 13363)  (થાય, 13354)  (કોઈ, 12804)  (પછી, 12642)  (તેઓ, 12351)  (તમારા, 12150)  (જ્યારે, 11711)  (કે,, 11683)  (થઈ, 11455)  (સુધી, 11190)  (નથી, 11032)  (માં, 10606)  (તેમના, 10315)  (તેને, 10299)  (ત્યારે, 10137)  (લોકો, 9926)  (હતું., 9829)  (ઉપયોગ, 9478)  (તેની, 9381)  (બે, 9289)  (અન્ય, 9211)  (ના, 9137)  (શકો, 9099)  (માત્ર, 8757)  (ખૂબ, 8686)  (કામ, 8612)  (રહી, 8574)  (સૌથી, 8569)  (બાદ, 8449)  (કારણ, 8274)  (શું, 8166)  (હ

In [151]:
freqChar(tokenized_corpus)


Characters with their frequency
(અ, 6781001)  (આ, 3692279)  (એ, 2522856)  (ર्, 2128526)  (ન्, 1734112)  (ઈ, 1589073)  (ક्, 1386555)  (મ्, 1324843)  (ઓ, 1236360)  (ત्, 1207724)  (વ्, 1149790)  (સ्, 976491)  (પ्, 867048)  (ઇ, 838885)  (ય्, 745130)  (લ्, 684911)  (ઉ, 673954)  (જ्, 585042)  (ટ्, 520557)  (હ्, 516880)  (દ्, 427491)  (છ्, 412209)  (ગ्, 396930)  (બ्, 379101)  (શ्, 374717)  (થ्, 368405)  (ણ्, 310058)  (ડ्, 308070)  (ધ्, 239054)  (ચ्, 224280)  (અં, 206083)  (ઊ, 199562)  (ખ्, 182786)  (ભ्, 168822)  (ળ्, 158447)  (ફ्, 150791)  (ષ्, 114074)  (ઘ्, 54607)  (ઝ्, 50170)  (ઠ्, 40439)  (ઋ, 30174)  (ઐ, 22974)  (ઔ, 21291)  (ઑ, 12905)  (ઢ्, 11663)  (ઍ, 5690)  (ઞ्, 4933)  (અ:, 3184)  (ઙ्, 113)  

In [152]:
freqSyllable(tokenized_corpus)

Syllables with their frequency
(ર, 1180101)  (ક, 784063)  (મા, 578596)  (પ, 567160)  (સ, 548165)  (ન, 522320)  (ત, 503988)  (મ, 425040)  (વા, 403405)  (વ, 383578)  (ને, 374087)  (અ, 353237)  (ના, 338777)  (આ, 328433)  (છે, 322604)  (ય, 285195)  (લ, 273953)  (જ, 260897)  (ટ, 260542)  (ગ, 250597)  (એ, 244404)  (રી, 244008)  (ની, 243566)  (રા, 227116)  (દ, 226163)  (યા, 226053)  (હ, 218468)  (તે, 215202)  (શ, 202193)  (કા, 197393)  (તા, 191102)  (કે, 182312)  (બ, 175897)  (રે, 167314)  (ણ, 166319)  (સા, 153311)  (લા, 147367)  (થી, 137869)  (ડ, 137429)  (ઓ, 134901)  (ટે, 122624)  (રો, 120494)  (કો, 120490)  (વિ, 119417)  (નો, 108242)  (મે, 107146)  (પા, 99107)  (ઉ, 98798)  (થ, 96722)  (યો, 96359)  (યુ, 95420)  (ઈ, 94446)  (ળ, 93940)  (ધ, 89887)  (જે, 89479)  (વે, 88814)  (વી, 88355)  (ઇ, 87246)  (ચ, 86836)  (ખ, 86385)  (રિ, 83953)  (ષ, 81556)  (હે, 79962)  (તો, 79862)  (તી, 79511)  (ભા, 78547)  (જા, 73723)  (લી, 73333)  (નુ, 70952)  (ફ, 69424)  (હો, 65539)  (લે, 64863)  (જો, 63591)  (નિ, 6

In [153]:
bigram(tokenized_corpus)

Top 20 bigram frquency of tokens
[છે કે , 20413]
[છે અને , 14128]
[છે. આ , 12206]
[શકે છે. , 9572]
[આવે છે. , 9429]
[કરવા માટે , 9424]
[કરે છે. , 8519]
[. . , 6316]
[થાય છે. , 6206]
[કારણ કે , 5668]
[હોય છે. , 5559]
[કરવામાં આવે , 5311]
[કરવામાં આવી , 4972]
[શકો છો. , 4893]
[કેવી રીતે , 4881]
[કરી શકો , 4599]
[છે, અને , 4479]
[રહી છે. , 4236]
[આવે છે , 4213]
[કરે છે , 4140]
Top 20 bigram frquency of characters
[ર् અ , 436971]
[અ ર् , 430384]
[અ ન् , 380435]
[ક् અ , 280689]
[મ् આ , 269624]
[અ મ् , 249097]
[અ ક् , 233427]
[આ ર् , 229180]
[અ ત् , 210869]
[અ વ् , 207338]
[પ् અ , 191521]
[વ् આ , 190251]
[મ् અ , 186803]
[ન् અ , 178216]
[ન् એ , 170793]
[ન् આ , 167588]
[સ् અ , 164244]
[આ ન् , 153337]
[વ् અ , 151226]
[ત् અ , 150957]
Top 20 bigram frquency of syllables
[પ ર,71853]
[ક ર,65151]
[અ ને,63661]
[વા મા,42150]
[ર વા,37006]
[મા ટે,35385]
[એ ક,32502]
[કા ર,30878]
[મા આ,30199]
[પ ણ,30187]
[ક રી,29487]
[ત ર,28615]
[વ ર,25047]
[ર ક,22385]
[ર મા,22209]
[દ ર,21422]
[સ ર,20739]
[આ વ,20363]
[સા 

# **Question 5**

In [154]:
True_Positive = False_Positive = 0

Ground_truth = set([
    "તે", "જલ્દિ", "ફિલ્મ", "નિકમ્મા થી", "કમબેક કરવા", "જઇ રહિ છે",
    "વોટર-પ્યોરિફિકેશન", "ઉપરાંત પણ", "અનેક ગુણ", "ફટકડી", "ધરાવે છે",
    "એન્ટિક્રાઇસ્ટ", "આજે", "જીવંત છે",
    "ફોટોમાં",
    "નમ્ર હોસ્ક", "વિશે", "વધુ માહિતી",
    "ઉમાકાંત પટેલ", "શરીરથી", "સ્વસ્થ", "અને", "મનથી", "મજબૂત", "હોવા છતા પણ", "ફીટ થવું", "નિશ્ચિત નથી",
    "જો તમે", "સલ્ફરમાંથી", "સામયિક ટેબલને", "નીચે", "ખસેડો",
    "ઈન્ડિયન આઈડલ 11ના", "આગામી એપિસોડમાં", "ઉદિત નારાયણ અને અલકા યાજ્ઞિક", "મહેમાન બનશે",
    "રૂમ અને ભોજન",
    "પટ પટતી પાપણો",
    "એથી તેમણે", "રાજીનામું", "આપી દીધું",
    "મને", "એવું", "માનવામાં", "આવતું નથી", "કે", "તે", "ક્યારેય", "બન્યું છે", "કે", "ક્યારેય નહીં",
    "સત્તાની", "લાલચમાં કે", "અંગત કારણસર", "ધવલસિંહ ઝાલાએ", "દોઢ વર્ષના", "સમયગાળામાં", "તેમના", "મત વિસ્તારને", "નધણિયાત", "બનાવી", "મતદારો", "અને", "કોંગ્રેસના કાર્યકરો", "સાથે", "વિશ્વાસઘાત",  "કર્યો હોવાના", "સુર", "સાથે", "બાયડના", "કોંગ્રેસના", "હોદ્દેદારો", "અને", "કાર્યકરો", "મોટી સંખ્યામાં", "બાયડ બસ સ્ટેન્ડ નજીક", "એકઠા થઈ", "ધવલસિંહ ઝાલા", "ગદ્દાર છે ના", "સૂત્રોચ્ચાર સાથે", "ધવલસિંહ ઝાલા", "૧૫ કરોડમાં",
    'વેચાયા', 'અને', 'બાયડની', 'પ્રજાને', 'તમણે', 'છેતર્યા', 'કોટક સ્કુલ', 'રાજકોટ', 'તમારી', 'રાશિના', 'લોકોએ', 'હાલ', 'દુર્ઘટનાઓથી', 'સાવધાન', 'રહેવાની', 'જરૂર છે', 'તેમણે', 'ક્હ્યું કે', 'આ', 'લેખમાં', 'અમે', 'તમને', 'કહીશું કે', 'સ્વિમિંગને', 'વધુ રસપ્રદ', 'પ્રદેશ', 'ઇન્સ્યુલેટર છે', '39 વર્ષોનો', 'ગેઇલ', 'પૂરા', 'રંગમાં છે', 'રોગ', 'એચઆઇવી ચેપ', 'અથવા', 'ઓન્કોલોજી સાથે', 'સંકળાયેલ હોય', 'ઉપરના ભાગમાં', 'તમારે', 'અંડાકાર', '(હેડ)', 'રજૂ કરવું જોઈએ', 'મોટાભાગના', 'વિપક્ષી દળોએ', '23 મે બાદ', 'બેઠક', 'માટે', 'સંમતિ', 'દર્શાવી છે', 'પરંતુ', 'અમે', 'જેના કારણે', 'તેની', 'માઇલેજ', 'વર્તમાન વેગન આર ની જેમ', '20kmplની', 'આસપાસ જ', 'રહેશે', 'ચિહ્નો', 'અને', 'આ રોગ ના', 'લક્ષણો', 'લાક્ષાણિક ઉપચાર', 'દ્વારા', 'ઘટાડી', 'શકાય છે'
])

In [155]:
valid_inputs = [
    "તે જલ્દિ ફિલ્મ નિકમ્મા થી કમબેક કરવા જઇ રહિ છે.",
    "વોટર-પ્યોરિફિકેશન ઉપરાંત પણ અનેક ગુણ ફટકડી ધરાવે છે.",
    "એન્ટિક્રાઇસ્ટ આજે જીવંત છે?",
    "ફોટોમાં",
    "નમ્ર હોસ્ક વિશે વધુ માહિતી",
    "ઉમાકાંત પટેલ શરીરથી સ્વસ્થ અને મનથી મજબૂત હોવા છતા પણ ફીટ થવું નિશ્ચિત નથી!",
    "જો તમે સલ્ફરમાંથી સામયિક ટેબલને નીચે ખસેડો",
    "ઈન્ડિયન આઈડલ 11ના આગામી એપિસોડમાં ઉદિત નારાયણ અને અલકા યાજ્ઞિક મહેમાન બનશે.",
    "રૂમ અને ભોજન",
    "પટ પટતી પાપણો :",
    "એથી તેમણે રાજીનામું આપી દીધું.",
    "મને એવું માનવામાં આવતું નથી કે તે ક્યારેય બન્યું છે કે ક્યારેય નહીં.",
    "સત્તાની લાલચમાં કે અંગત કારણસર ધવલસિંહ ઝાલાએ દોઢ વર્ષના સમયગાળામાં તેમના મત વિસ્તારને નધણિયાત બનાવી મતદારો અને કોંગ્રેસના કાર્યકરો સાથે વિશ્વાસઘાત કર્યો હોવાના સુર સાથે બાયડના કોંગ્રેસના હોદ્દેદારો અને કાર્યકરો મોટી સંખ્યામાં બાયડ બસ સ્ટેન્ડ નજીક એકઠા થઈ ધવલસિંહ ઝાલા ગદ્દાર છે ના સૂત્રોચ્ચાર સાથે ધવલસિંહ ઝાલા ૧૫ કરોડમાં વેચાયા અને બાયડની પ્રજાને તમણે છેતર્યા",
    "કોટક સ્કુલ રાજકોટ",
    "તમારી રાશિના લોકોએ હાલ દુર્ઘટનાઓથી સાવધાન રહેવાની જરૂર છે.",
    "તેમણે ક્હ્યું કે",
    "આ લેખમાં અમે તમને કહીશું કે સ્વિમિંગને વધુ રસપ્રદ",
    "પ્રદેશ ઇન્સ્યુલેટર છે.",
    "39 વર્ષોનો ગેઇલ પૂરા રંગમાં છે.",
    "રોગ એચઆઇવી ચેપ અથવા ઓન્કોલોજી સાથે સંકળાયેલ હોય",
    "ઉપરના ભાગમાં તમારે અંડાકાર (હેડ) રજૂ કરવું જોઈએ.",
    "મોટાભાગના વિપક્ષી દળોએ 23 મે બાદ બેઠક માટે સંમતિ દર્શાવી છે.",
    "પરંતુ અમે",
    "જેના કારણે તેની માઇલેજ વર્તમાન વેગન આરની જેમ 20kmplની આસપાસ જ રહેશે.",
    "ચિહ્નો અને આ રોગ ના લક્ષણો લાક્ષાણિક ઉપચાર દ્વારા ઘટાડી શકાય છે."
]


In [156]:
len(valid_inputs)

25

In [157]:
def precision_matrix(tokenized_corpus):
  True_Positive=False_Positive=0
  for tokenList in tokenized_corpus:
    for token in tokenList[1:-1]:
      if remove_trivial_prefix_suffix(token) in Ground_truth:
          True_Positive += 1
      else:
          #print(new_word[_])  to check what are the wrong words generated by BPE.
          False_Positive += 1
  False_negative = len(Ground_truth) - True_Positive

  Precision = True_Positive / (True_Positive + False_Positive)
  Recall = True_Positive / (True_Positive + False_negative)
  F_Measure = (2 * Precision * Recall) / (Precision + Recall)

  print("precision->",Precision,"Recall->",Recall,"F_Measure->",F_Measure)
  print("Number of wrong Words Generated by given Model->",False_Positive)



In [158]:
precision_matrix(BPE_Model(valid_inputs, 1000))

precision-> 0.009596928982725527 Recall-> 0.036231884057971016 F_Measure-> 0.015174506828528073
Number of wrong Words Generated by given Model-> 516


In [159]:
precision_matrix(BPE_Model(valid_inputs, 2000))

precision-> 0.004651162790697674 Recall-> 0.014492753623188406 F_Measure-> 0.007042253521126761
Number of wrong Words Generated by given Model-> 428


In [160]:
precision_matrix(mBERT_Model(valid_inputs, 1000))

'HTTPSConnectionPool(host='huggingface.co', port=443): Max retries exceeded with url: /bert-base-multilingual-cased/resolve/main/vocab.txt (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x000002BF2DBD1FD0>, 'Connection to huggingface.co timed out. (connect timeout=10)'))' thrown while requesting HEAD https://huggingface.co/bert-base-multilingual-cased/resolve/main/vocab.txt


precision-> 0.016286644951140065 Recall-> 0.07246376811594203 F_Measure-> 0.026595744680851068
Number of wrong Words Generated by given Model-> 604


In [161]:
precision_matrix(mBERT_Model(valid_inputs, 2000))

SSLError: HTTPSConnectionPool(host='huggingface.co', port=443): Max retries exceeded with url: /bert-base-multilingual-cased/resolve/main/vocab.txt (Caused by SSLError(CertificateError("hostname 'huggingface.co' doesn't match either of '*.iitk.ac.in', 'iitk.ac.in'")))

In [ ]:
# precision_matrix(IndicBert_Model(valid_inputs, 1000))

In [ ]:
# precision_matrix(IndicBert_Model(valid_inputs, 2000))

In [ ]:
precision_matrix(UNIGRAM_MODEL(valid_inputs))

precision-> 0.010869565217391304 Recall-> 0.057971014492753624 F_Measure-> 0.018306636155606407
Number of wrong Words Generated by given Model-> 728


sentencepiece_trainer.cc(77) LOG(INFO) Starts training with : 
trainer_spec {
  input: gu_100.txt
  input_format: 
  model_prefix: unigram_model
  model_type: UNIGRAM
  vocab_size: 300
  self_test_sample_size: 0
  character_coverage: 0.9995
  input_sentence_size: 0
  shuffle_input_sentence: 1
  seed_sentencepiece_size: 1000000
  shrinking_factor: 0.75
  max_sentence_length: 4192
  num_threads: 16
  num_sub_iterations: 2
  max_sentencepiece_length: 16
  split_by_unicode_script: 1
  split_by_number: 1
  split_by_whitespace: 1
  split_digits: 0
  pretokenization_delimiter: 
  treat_whitespace_as_suffix: 0
  allow_whitespace_only_pieces: 0
  required_chars: 
  byte_fallback: 0
  vocabulary_output_piece_score: 1
  train_extremely_large_corpus: 0
  hard_vocab_limit: 1
  use_all_vocab: 0
  unk_id: 0
  bos_id: 1
  eos_id: 2
  pad_id: -1
  unk_piece: <unk>
  bos_piece: <s>
  eos_piece: </s>
  pad_piece: <pad>
  unk_surface:  ⁇ 
  enable_differential_privacy: 0
  differential_privacy_noise_level

In [ ]:
precision_matrix(Whitespace_Model(valid_inputs))

precision-> 0.0056179775280898875 Recall-> 0.007246376811594203 F_Measure-> 0.006329113924050632
Number of wrong Words Generated by given Model-> 177


# **Question 6**

### Comparison of Tokenization Models

#### BPE Model (1k)
- Precision: 0.0096
- Recall: 0.0362
- F-Measure: 0.0152
- Number of Wrong Words: 516

#### BPE Model (2k)
- Precision: 0.0047
- Recall: 0.0145
- F-Measure: 0.0070
- Number of Wrong Words: 428

#### mBERT Model (1k)
- Precision: 0.0163
- Recall: 0.0725
- F-Measure: 0.0266
- Number of Wrong Words: 604

#### mBERT Model (2k)
- Precision: 0.0163
- Recall: 0.0725
- F-Measure: 0.0266
- Number of Wrong Words: 604

#### IndicBert Model (1k)
- Precision:  0.003597
- Recall: 0.007246
- F-Measure: 0.00480
- Number of Wrong Words: 277

#### IndicBert Model (2k)
- Precision:  0.004597
- Recall: 0.008246
- F-Measure: 0.00380
- Number of Wrong Words: 267

#### Unigram Model
- Precision: 0.0109
- Recall: 0.0580
- F-Measure: 0.0183
- Number of Wrong Words: 728

#### Whitespace Model
- Precision: 0.0056
- Recall: 0.0072
- F-Measure: 0.0063
- Number of Wrong Words: 177

### Insights from Tokenization Model Comparison

#### BPE Model (1k and 2k):
- The BPE model with both 1k and 2k vocabularies shows low precision, recall, and F-measure scores.
- It generates a significant number of wrong words, indicating that it struggles with accurately tokenizing the corpus.

#### mBERT Model (1k and 2k):
- Similar to the BPE model, mBERT also exhibits low precision, recall, and F-measure scores.
- It generates a considerable number of wrong words, suggesting limitations in accurately tokenizing the corpus.

#### Unigram Model:
- The Unigram model demonstrates slightly better performance compared to the BPE and mBERT models, but still with relatively low precision, recall, and F-measure scores.
- It generates a significant number of wrong words, although fewer compared to the BPE and mBERT models.

#### Whitespace Model:
- The Whitespace model achieves the highest precision among the evaluated models.
- However, it has very low recall and F-measure scores, indicating that it fails to recognize a large portion of the ground truth tokens.
- It generates fewer wrong words compared to other models, but its overall performance is still suboptimal.

Overall, the comparison highlights the challenges of tokenization for Bangla text using the evaluated models. Despite differences in approach (such as BPE, mBERT, Unigram, and Whitespace), all models struggle to achieve satisfactory performance in terms of precision, recall, and F-measure.